In [1]:
import sys
!{sys.executable} -m pip install numpy
!{sys.executable} -m pip install biopython
!{sys.executable} -m pip install pandas
!{sys.executable} -m pip install scikit-learn

In [5]:
from Bio import SeqIO
import sys
import numpy as np
import pandas as pd

cancer_genes = pd.read_csv("C:\\Users\\monju\\OneDrive\\bioinformatics-data\\cancer_genes_latest.csv")
cell_line_details = pd.read_excel("C:\\Users\\monju\\OneDrive\\bioinformatics-data\\cell_line_details.xlsx")
cosmic_tissue_classification = pd.read_excel("C:\\Users\\monju\\OneDrive\\bioinformatics-data\\cosmic_tissue_classification.xlsx")
gdsc1 = pd.read_excel("C:\\Users\\monju\\OneDrive\\bioinformatics-data\\gdsc1_fitted_dose_response.xlsx")
gdsc2 = pd.read_excel("C:\\Users\\monju\\OneDrive\\bioinformatics-data\\gdsc2_fitted_dose_response.xlsx")
gene_identifiers_modified = pd.read_csv("C:\\Users\\monju\\OneDrive\\bioinformatics-data\\gene_identifiers_modified.csv")
model_list = pd.read_csv("C:\\Users\\monju\\OneDrive\\bioinformatics-data\\model_list_latest.csv")
mutations_latest = pd.read_csv("C:\\Users\\monju\\OneDrive\\bioinformatics-data\\mutations_latest.csv")
screened_compounds = pd.read_csv("C:\\Users\\monju\\OneDrive\\bioinformatics-data\\screened_compounds_rel_8.0.csv")
pancancer_genetic_features = pd.read_csv("C:\\Users\\monju\\OneDrive\\bioinformatics-data\\pan_cancer_genetic_feature.csv")


In [49]:
#create cosmic tissue classification map
#create gene identifiers map with gene id, (will help in GDSC1)
cosmic_tissue_classification_map_with_cosmic_id = {}
gene_identifiers_map_with_sanger_id = {}
screened_compounds_map_with_drug_id = {}
cell_line_details_map_with_cosmic_id = {}
pan_cancer_map_with_cosmic_id={}
mutations_map_with_model_id={}
mutations_map_with_genes = {}
cancer_gene_map_with_symbol={}
drug_id_map_with_gdsc1 = {}
cancer_gene_set = set({})
drugs_set = set({})

for index, row in pancancer_genetic_features.iterrows():
    pan_cancer_map_with_cosmic_id[row['cosmic_sample_id']] = row
    
for index, row in gdsc1.iterrows():
    if row['COSMIC_ID'] in pan_cancer_map_with_cosmic_id:
        if row['Z_SCORE']<=2.0:
            drugs_set.add(row['DRUG_ID'])
            if row['DRUG_ID'] not in drug_id_map_with_gdsc1:
                drug_related_data = []
                drug_related_data.append(row)
                drug_id_map_with_gdsc1[row['DRUG_ID']]=drug_related_data
            else:
                drug_related_data = drug_id_map_with_gdsc1[row['DRUG_ID']]
                drug_related_data.append(row)
                drug_id_map_with_gdsc1[row['DRUG_ID']]=drug_related_data

for index, row in cancer_genes.iterrows():
    cancer_gene_map_with_symbol[row['gene_symbol']]=row
    cancer_gene_set.add(row['gene_symbol'])

for index, row in cosmic_tissue_classification.iterrows():
    cosmic_tissue_classification_map_with_cosmic_id[row['cosmic_id']]=row
    
for index, row in gene_identifiers_modified.iterrows():
    gene_identifiers_map_with_sanger_id[row['gene_id']]=row
    
for index, row in screened_compounds.iterrows():
    screened_compounds_map_with_drug_id[row['DRUG_ID']]=row
    
for index, row in cell_line_details.iterrows():
    cell_line_details_map_with_cosmic_id[row['cosmic_identifier']]=row
    
for index, row in mutations_latest.iterrows():
    if row['model_id'] not in mutations_map_with_model_id:
        model_genes = []
        model_genes.append(row)
        mutations_map_with_model_id[row['model_id']] = model_genes
        model_gene_symbols = []
        model_gene_symbols.append(row['gene_symbol'])
        mutations_map_with_genes[row['model_id']]=model_gene_symbols
    else:
        model_genes = mutations_map_with_model_id[row['model_id']]
        model_genes.append(row)
        mutations_map_with_model_id[row['model_id']]=model_genes
        model_gene_symbols = mutations_map_with_genes[row['model_id']]
        model_gene_symbols.append(row['gene_symbol'])
        mutations_map_with_genes[row['model_id']]=model_gene_symbols

In [50]:
gene_expression_data = []

for d in sorted(drugs_set):
    
    if d in drug_id_map_with_gdsc1:
        for g in drug_id_map_with_gdsc1[d]:
            data = []
            data.append(d)
            print(g.Z_SCORE)
            for index, row in cancer_genes.iterrows():
                if g.SANGER_MODEL_ID in mutations_map_with_genes:
                    model_genes = mutations_map_with_genes[g.SANGER_MODEL_ID]
                    if row['gene_symbol'] in model_genes:
                        data.append(1)
                    else:
                        data.append(0)
                else:
                    data.append(0)
                
            
            data.append(g.Z_SCORE)
            gene_expression_data.append(data)
        
                

-0.192056
0.505823
1.28075
0.086028
-0.114395
-0.530674
1.29759
0.342749
-0.099233
0.940093
1.195692
1.025987
-5.365666
0.618134
-0.259559
1.237079
1.013655
0.799717
0.651928
0.765362
0.152193
-0.841048
0.520152
0.02212
0.793868
1.472805
0.41995
0.118789
0.023999
1.290696
-0.708156
0.474551
0.483337
0.425394
1.022397
0.757404
0.383404
0.204508
-1.541141
0.297426
-1.910497
0.33599
0.177897
-1.107541
0.902927
-4.169452
1.093047
-0.777487
-0.069282
-0.081695
-0.640532
-0.352945
-0.415918
-0.166512
0.764377
0.155527
0.392444
1.19139
-1.436908
-2.461419
-0.789511
-0.89958
-0.43981
-1.153052
-0.420345
-4.12224
1.330239
1.490723
-0.752562
-0.733876
-0.757173
0.848934
1.94824
0.578721
0.780033
1.101098
-1.519578
-0.396797
0.339085
0.732153
-3.741583
-1.212671
-0.710954
0.701901
0.056402
0.390223
0.51128
0.117548
0.74403
-0.22118
0.282629
0.017068
-1.372596
-3.462395
0.47529
0.144328
0.653802
0.495638
-0.320092
-2.690996
1.305099
-0.121666
0.7844
0.177475
-1.346184
-1.150802
-0.001265
0.226282


-0.486059
1.500441
0.148419
0.139809
-1.037715
-0.572203
-0.439004
-0.777962
-0.356369
0.647146
-0.434081
-0.528862
-0.163863
-0.608107
0.116254
-0.891716
0.072174
1.303584
1.56646
0.212459
-1.085249
-1.036904
-0.500885
0.647736
-0.709901
-0.399283
0.586252
-0.558748
-0.685658
1.203935
-0.704461
-0.755194
-0.661661
-1.148892
0.348424
-0.091079
-0.552309
-0.895959
-1.508139
-0.425626
1.057168
-0.143658
-0.09042
-0.024297
-0.104876
0.57959
-0.562334
-0.382358
0.145312
-0.448795
-0.948927
0.065854
0.082362
-3.293396
1.530669
0.336131
0.481687
0.051605
-4.245278
-0.881995
-1.039944
0.274147
-0.38566
1.625031
-0.908609
0.84508
-2.775002
0.260911
-0.082636
-0.748113
0.063505
-0.596225
-0.396669
0.69552
0.808703
1.592752
-0.105243
1.459405
1.094584
0.777262
0.694344
1.447609
-0.116885
-0.819592
-0.48572
0.150136
0.769988
-0.331187
-0.892506
0.412221
-0.009936
0.532268
-0.342437
-0.056124
-1.008356
-1.114422
0.56808
-0.930983
-0.642911
-1.288446
-0.123196
-0.62764
1.135869
0.367929
-0.18769
0.

0.955489
-1.903802
-1.759804
-0.581037
1.599823
-0.165393
0.557697
0.709173
1.791265
0.32946
0.667677
0.019034
0.52332
-1.403306
-1.461023
-0.584752
1.307536
0.937116
-1.609069
-1.174963
-0.097778
1.602794
-0.274571
-0.755822
0.365024
-0.348053
1.390647
-0.669124
-2.033736
-0.682745
-0.207375
-0.672682
0.887104
-0.75472
-1.486823
-0.285554
1.75147
-0.279858
-1.041833
0.353164
1.703023
-0.02597
1.772411
1.539938
-0.387102
1.530284
0.043654
-1.129773
-0.187601
0.067739
0.082625
-1.195341
1.034785
-1.10775
0.181125
0.211257
0.728938
-1.186295
0.085857
1.02825
-1.665898
-0.745777
1.502862
-1.774103
0.243383
-0.197007
1.017
0.07922
1.025561
1.919379
-0.112499
0.290617
-2.874559
-0.266365
-0.978249
1.096988
-1.018516
-0.386468
-0.092388
-1.601953
-1.463756
-0.745418
-0.95452
1.041408
0.705811
0.52824
-0.451024
-0.260386
-1.290836
0.16001
-1.028766
-1.678523
0.185752
1.229212
-1.758205
-0.768018
0.098698
-0.219236
-1.106852
0.417992
0.213816
0.839507
0.802929
1.337845
1.803424
-2.049595
-1.00

1.08606
0.473316
0.255598
-0.627884
0.587185
1.096174
0.733111
-1.591273
-0.939788
0.426534
0.113095
0.906648
0.848739
-1.060555
0.242786
-0.64302
1.028219
0.357744
0.323099
0.974671
0.187165
-1.49694
0.585548
0.095241
-0.938948
-0.328314
0.748836
-0.269387
0.900984
-0.582407
-0.124643
-0.81017
-0.274444
0.871914
0.120236
0.729525
0.591839
0.623855
0.542409
1.02638
0.952975
-0.113577
1.063351
0.166106
1.368758
0.875569
0.631378
-0.040433
0.114629
-0.019943
0.427023
-0.789851
0.62852
0.570635
0.746571
1.045203
-0.602721
-0.003468
0.335735
0.190106
0.326933
1.134707
-0.820651
-0.367781
0.260257
-0.59891
-0.005972
-1.110086
0.835667
0.528934
-2.047379
0.200496
-0.404916
0.261652
-0.344771
-2.123078
-0.166741
-0.66234
0.167429
-1.6165
-1.644967
-0.420362
0.98466
-1.538613
0.249195
-1.607719
0.963681
-0.72615
-1.367207
-0.294739
-0.009972
-0.338268
-2.463938
0.867872
0.371885
1.06357
0.441581
-0.960599
-2.549386
-2.60123
0.277615
-0.35543
-0.166727
0.074956
-1.604722
-2.959531
0.270821
0.26

0.14526
-1.158773
-0.811679
-1.833514
-0.85858
-0.802965
-0.953203
-0.003873
-0.369861
0.777983
0.062646
-0.850174
-0.952728
-0.752279
-1.552293
-0.490359
0.094411
-0.380262
-0.323258
-2.37725
0.176905
-0.22067
0.820168
1.364107
0.975798
1.452568
-1.828489
1.319308
1.202419
-0.012908
-0.347549
1.233698
-0.642505
-0.596358
0.350171
1.6952
0.965022
0.559253
-0.192192
0.751252
-0.803634
-0.78697
-0.531668
0.559719
-0.264806
0.637489
-0.096847
0.041705
0.749199
0.416613
-0.406879
-0.508923
0.171623
-1.412016
-0.278204
-0.450533
0.461028
1.345426
0.182154
0.958748
0.640208
-0.637214
-1.002235
0.720946
1.232994
-1.562588
1.305347
-0.676142
1.035673
0.384332
-0.90307
1.1795
0.577306
-0.368944
-0.696769
0.862399
-0.749938
0.242783
-0.370004
-0.110631
0.403011
0.400051
-1.723732
1.087209
0.48784
0.473529
-0.247569
1.128935
-1.466338
0.882271
-0.366717
0.038003
1.633537
-0.547139
-1.20823
0.746986
-0.794527
-0.036874
0.291603
1.22251
-0.326096
-0.561671
-0.836137
-0.110003
-0.971638
0.949005
0.8

...

-0.170659
0.621378
0.670794
-1.433136
0.753625
0.941626
0.141992
0.060305
0.001387
0.313179
-0.097457
-0.264965
-0.772152
-1.043047
-1.139034
-0.044833
-0.133722
-0.082951
1.031939
-1.432616
-1.858583
-1.43081
1.667022
0.20307
-0.605762
-0.177555
-0.921741
-0.860683
-0.582063
-1.107602
0.935118
-3.87474
-1.569076
-1.951746
-0.809417
-1.060618
-1.262066
-0.922369
-0.404103
-0.01216
-1.037769
-0.287492
-0.809886
0.286574
0.303867
-1.593284
0.145159
-0.083058
-0.307831
-0.934492
-0.378218
1.199001
-0.98013
-0.016002
0.468254
0.089963
0.113612
-0.534872
-2.203344
-1.933565
-0.884084
0.999154
-0.27896
-1.393544
-1.687625
-0.796931
-0.702798
-1.549338
-1.157006
-1.507151
-0.059152
-0.268423
-1.770498
0.47734
-0.13755
-0.442665
-0.102577
-0.808925
0.189887
0.308706
-0.205616
-2.28092
0.001592
-0.554612
-0.248889
-0.168522
-1.063043
-0.192066
-0.72443
0.23722
-1.244538
-0.678687
-0.834468
-0.834483
1.147062
-0.534498
0.8023
0.698412
-0.489908
0.74849
-1.046572
0.879573
0.026689
0.497396
-1.221

-2.045474
0.815672
1.383552
-2.235772
-0.129184
1.333253
0.482711
-0.544223
-1.55857
1.270074
-0.065037
1.31789
0.007874
0.897308
-0.352508
-0.101686
-0.044524
-1.998257
1.537803
0.945728
0.913059
0.118495
-0.136317
0.783715
-1.556713
0.264249
1.320197
-1.251582
0.619985
-0.903605
0.399036
1.161634
0.381399
1.622996
-2.092833
1.079194
0.820291
-1.90376
0.839835
-1.07727
1.233155
-0.138551
-0.149614
-0.225179
1.057011
-0.860293
1.352524
0.164976
-1.571111
0.10388
-0.076121
0.807762
1.719354
-2.534446
-1.041246
0.286306
0.563054
0.832356
-0.115755
0.880863
1.103932
0.919789
-0.403911
-0.018622
0.491295
-0.049809
0.340564
0.089347
0.725933
-0.299648
0.099137
0.644699
0.20447
0.894349
0.562106
0.557188
1.400626
-0.364787
-2.187048
1.198692
0.99186
1.558845
-0.919257
-1.199485
1.074252
-0.672558
-0.188928
1.107278
0.382688
0.913795
-0.566949
-1.042064
-1.295424
-0.369269
-0.161471
0.182861
-0.466581
-1.419112
-0.346267
1.555289
-0.002316
-0.470489
-1.462228
-1.379103
0.451932
-1.628257
0.12

0.977944
1.217599
-3.552271
0.157664
1.191828
0.471817
0.440803
0.937828
0.719874
0.01502
0.910875
0.530323
-0.526386
-0.308889
0.912096
0.340935
1.126749
1.456128
0.569327
-3.230425
-1.064225
-0.222989
0.624732
0.263625
0.466997
0.185172
-1.589208
0.381375
-0.284956
-0.466932
-2.447096
0.134711
-0.355487
0.409791
0.520473
0.093299
0.847718
-1.354617
-0.051912
0.212736
0.215396
0.525463
-0.083333
-2.253043
0.131553
-0.559508
1.408009
-0.512547
0.270633
-0.199076
1.338539
-0.416046
1.046569
0.337718
-2.384709
-0.304759
1.0777
0.4982
0.679035
0.698801
0.919755
0.75304
0.927676
-0.337808
0.165173
0.562125
0.683343
0.841909
0.23456
0.212917
-0.087323
-1.644288
0.448216
0.985547
0.233907
-0.231785
0.582254
0.121922
0.311606
0.228282
-0.12648
-1.122373
0.538826
-0.060268
0.587599
-1.779851
-1.106528
0.471937
0.363006
0.716861
-2.279047
0.407691
0.61159
0.774776
0.555295
0.514067
0.696001
0.84612
-1.946034
0.478941
-0.769538
0.316044
0.712389
0.592333
1.798178
0.150423
0.342824
0.202186
0.368

0.83641
0.664945
-0.025564
-0.545573
0.743224
-0.764197
0.280179
0.102691
0.135977
0.222506
0.084134
0.776811
0.295636
-0.719745
0.625186
1.341094
-0.100396
0.118242
-0.156161
1.426453
1.178123
-2.051798
0.910716
0.615916
-0.075756
-0.276165
0.816726
-0.371183
-0.441687
0.317802
-0.017117
1.576416
-0.958328
0.335497
-0.316788
0.755135
1.313844
-0.544297
-1.401198
0.148911
-0.324607
-0.094205
1.574129
0.380531
1.56479
-0.670814
1.966435
1.379443
-0.033322
-1.239449
0.672184
1.468023
-0.284208
-0.642452
0.535171
-1.082276
0.042647
0.004726
0.359981
0.895204
0.099512
-0.480771
-0.087921
-1.03045
1.288002
-0.023518
-1.372359
0.497107
1.68363
0.892001
1.922324
-0.73961
-1.513513
0.635315
-0.348479
-0.017576
0.105101
-0.738061
-0.233771
1.290295
-0.863555
-0.74575
1.132277
-0.606279
-0.337813
0.430243
-1.269476
1.39398
-0.410075
0.518621
-0.315347
-1.14954
-0.761328
1.190972
-0.389001
-0.676248
-0.130147
-0.310991
-0.859491
-0.058415
0.006345
0.155287
0.673947
0.23037
-0.229395
1.37509
-0.83

KeyboardInterrupt: 

In [48]:
gene_columns = ['drug_id']

for index, row in cancer_genes.iterrows():
    gene_columns.append(row['gene_symbol'])
gene_columns.append('z_score')    
gene_drug_response_data_frame = pd.DataFrame(gene_expression_data,columns= gene_columns)
gene_drug_response_data_frame.to_csv('C:\\Users\\monju\\OneDrive\\bioinformatics-data\\gene_drug_response.csv')

[[1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, -5.365666], [1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

In [3]:
from Bio import Entrez

cancer_gene_sequences = {};
Entrez.email="monjurmorshed793@gmail.com"
counter = 0;
for index, row in cancer_genes.iterrows():
    counter +=1
    print(row[0])
    handle = Entrez.esearch(db='gene', term=row[0])
    record = Entrez.read(handle)
    for i in record['IdList']:
        executed = False
        try:
            gene_data = Entrez.efetch(db="nucleotide", id=i, rettype="fasta", retmode="fasta")
#             cancer_gene_sequences.append(gene_data.read)
            sequence = SeqIO.parse(gene_data, 'fasta')
            cancer_gene_sequences[row[0]]=str(gene_data.read())
            sequence_seq = next(sequence)
            gene_data_str = str(sequence_seq.seq)
            print('------')
            print(gene_data_str)
            if 'NNN' in gene_data_str:
                executed = False
            else:
                executed=True
#             f = open("C:\\Users\\monju\\Documents\\bioinformatics-data\\cancer_genes\\"+row[0]+".fasta","w")
#             f.write(next(sequence))
#             f.close()
        except:
            executed=False    
        if executed==True:
            break
  

ABCB1
ABL2
ACACA
ACVR1B
ACVR2A
ADCY1
ADGRL2
AFDN
AFF4
AHCTF1
AHNAK
AKAP9
AKT1
ALK
AMER1
AMOT
ANK3
APAF1
APC
AQR
ARAP3
ARFGAP3
ARFGEF1
ARFGEF2
ARHGAP26
ARHGAP29
ARHGEF6
ARID1A
ARID2
ARID4A
ARID4B
ARID5B
ASH1L
ASPM
ASXL1
ATM
ATR
ATRX
AXIN1
AXIN2
B2M
BAP1
BAZ2B
BCLAF1
BCOR
BLM
BMPR2
BNC2
BPTF
BRAF
BRCA1
BRCA2
BRWD1
CAD
CASP8
CCAR1
CCND1
CDC27
CDC73
CDH1
CDK12
CDKN1A
CDKN1B
CDKN2A
CEP290
CHD4
CHD6
CHD9
CIC
CLASP2
CLOCK
CLSPN
CMTR2
CNOT1
CNOT3
COL1A1
CREBBP
CTCF
CTNNB1
CTNND1
CUL2
CUL3
CUX1
CYLD
DDX3X
DDX5
DHX15
DHX9
DICER1
DLG1
DNMT3A
EGFR
EIF4G1
ELF1
ELF3
EPHA2
EPHA4
ERBB2
ERBB3
ERBIN
EZH2
F8
FAF1
FAT1
FAT2
FBXW7
FIP1L1
FLT3
FN1
FOXP1
FRG1BP
FXR1
G3BP2
GATA3
GNA11
GPS2
HDAC9
HGF
HLA-A
HLA-B
HNF1A
HRAS
HSPA8
IDH1
IDH2
INPP4A
INPPL1
IREB2
ITSN1
KALRN
KAT6B
KDM5C
KDM6A
KDR
KEAP1
KIT
KMT2A
KMT2D
KRAS
LAMA2
LARP4B
LIMA1
LNPEP
LRP6
LRPPRC
MACF1
MAGI2
MAP2K1
MAP2K4
MAP3K1
MAP3K4
MAP4K3
MAX
MCM3
MECOM
MED12
MED23
MED24
MET
MGA
MKL1
MLH1
MLH3
MNDA
MSR1
MTOR
MYC
MYCN
MYH11
MYH14
MYH9
NCOR1
NCOR2
NF